In [26]:
import pandas as pd
import os
from datetime import datetime, timedelta
import glob
import pandas as pd
import random
import numpy as np
import seaborn as sns
import ast
import json
import os
import re
import itertools
import folium
import hdbscan
import h3

from scipy.spatial.transform import Rotation as R
from scipy.spatial.distance import euclidean
from scipy.spatial.distance import pdist, squareform
from sklearn.cluster import DBSCAN
from sklearn.neighbors import NearestNeighbors
import matplotlib.pyplot as plt
import matplotlib.pylab as pl
import matplotlib.patches as patches
from pydp.algorithms.numerical_mechanisms import LaplaceMechanism
from itertools import combinations
from collections import defaultdict
from collections import Counter
from typing import Dict, Set, List, Optional, Tuple

In [27]:
df_gps = pd.read_csv("C:\\Users\\dmc\\Desktop\\extracted_trips_data.csv")

df_people = pd.read_csv("C:\\Users\\dmc\\Desktop\\individuals_dataset.csv")
df_people = df_people[df_people['GPS_RECORD'] == True]

df_merged = pd.merge(
    df_gps,
    df_people[['ID', 'SEX', 'AGE', 'PRO_CAT', 'WEIGHT_INDIV']],
    left_on='person_id',
    right_on='ID',
    how='inner'
).drop(columns='ID')

h3_resolution = 10

df_merged['start_h3'] = df_merged.apply(lambda row: h3.latlng_to_cell(row['start_lat'], row['start_lon'], h3_resolution), axis=1)
df_merged['end_h3'] = df_merged.apply(lambda row: h3.latlng_to_cell(row['end_lat'], row['end_lon'], h3_resolution), axis=1)

media_peso = df_merged['WEIGHT_INDIV'].mean()

In [28]:
# mode = "SEX"
mode = "AGE"
# mode = "PRO_CAT"

In [29]:
if mode == "SEX":
    df_man = df_merged[df_merged["SEX"] == "Man"]
    df_woman = df_merged[df_merged["SEX"] == "Woman"]
    print("Split fatto per SEX")
    
elif mode == "AGE":
    df_10_19 = df_merged[(df_merged["AGE"] >= 10) & (df_merged["AGE"] <= 19)]
    df_20_29 = df_merged[(df_merged["AGE"] >= 20) & (df_merged["AGE"] <= 29)]
    df_30_39 = df_merged[(df_merged["AGE"] >= 30) & (df_merged["AGE"] <= 39)]
    df_40_49 = df_merged[(df_merged["AGE"] >= 40) & (df_merged["AGE"] <= 49)]
    df_50_59 = df_merged[(df_merged["AGE"] >= 50) & (df_merged["AGE"] <= 59)]
    df_60_69 = df_merged[(df_merged["AGE"] >= 60) & (df_merged["AGE"] <= 69)]
    df_over70 = df_merged[(df_merged["AGE"] >= 70)]
    print("Split fatto per AGE")
    
elif mode == "PRO_CAT":
    df_procat_1 = df_merged[df_merged["PRO_CAT"] == 1]
    df_procat_2 = df_merged[df_merged["PRO_CAT"] == 2]
    df_procat_3 = df_merged[df_merged["PRO_CAT"] == 3]
    df_procat_4 = df_merged[df_merged["PRO_CAT"] == 4]
    df_procat_5 = df_merged[df_merged["PRO_CAT"] == 5]
    df_procat_6 = df_merged[df_merged["PRO_CAT"] == 6]
    df_procat_7 = df_merged[df_merged["PRO_CAT"] == 7]
    df_procat_8 = df_merged[df_merged["PRO_CAT"] == 8]
    print("Split fatto per PRO_CAT")
    
else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")

Split fatto per AGE


In [30]:
if mode == "SEX":
    od_matrix_first_man = df_man.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_man.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_woman = df_woman.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_woman.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

elif mode == "AGE":
    od_matrix_first_10_19 = df_10_19.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_10_19.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_20_29 = df_20_29.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_20_29.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_30_39 = df_30_39.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_30_39.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_40_49 = df_40_49.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_40_49.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_50_59 = df_50_59.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_50_59.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_60_69 = df_60_69.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_60_69.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_over70 = df_over70.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_over70.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

elif mode == "PRO_CAT":
    od_matrix_first_procat_1 = df_procat_1.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_procat_1.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_procat_2 = df_procat_2.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_procat_2.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_procat_3 = df_procat_3.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_procat_3.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_procat_4 = df_procat_4.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_procat_4.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_procat_5 = df_procat_5.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_procat_5.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_procat_6 = df_procat_6.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_procat_6.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_procat_7 = df_procat_7.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_procat_7.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_procat_8 = df_procat_8.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_procat_8.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")

In [31]:
parent_hexes = ["861fb4667ffffff", "861fb4677ffffff", "861fb466fffffff", "861fb4647ffffff", "861fb475fffffff"]

target_resolution = 10
start_valid_h3 = set()
end_valid_h3 = set()

for parent in parent_hexes:
    children = h3.cell_to_children(parent, target_resolution)
    for child in children:
        start_valid_h3.add(child)
        end_valid_h3.add(child)

if mode == "SEX":
    mask_man = ((od_matrix_first_man["start_h3"].isin(start_valid_h3)) & (od_matrix_first_man["end_h3"].isin(end_valid_h3)))
    mask_woman = ((od_matrix_first_woman["start_h3"].isin(start_valid_h3)) & (od_matrix_first_woman["end_h3"].isin(end_valid_h3)))

    od_matrix_first_man = od_matrix_first_man[mask_man].copy()
    od_matrix_first_woman = od_matrix_first_woman[mask_woman].copy()

elif mode == "AGE":
    mask_10_19 = ((od_matrix_first_10_19["start_h3"].isin(start_valid_h3)) & (od_matrix_first_10_19["end_h3"].isin(end_valid_h3)))
    mask_20_29 = ((od_matrix_first_20_29["start_h3"].isin(start_valid_h3)) & (od_matrix_first_20_29["end_h3"].isin(end_valid_h3)))
    mask_30_39 = ((od_matrix_first_30_39["start_h3"].isin(start_valid_h3)) & (od_matrix_first_30_39["end_h3"].isin(end_valid_h3)))
    mask_40_49 = ((od_matrix_first_40_49["start_h3"].isin(start_valid_h3)) & (od_matrix_first_40_49["end_h3"].isin(end_valid_h3)))
    mask_50_59 = ((od_matrix_first_50_59["start_h3"].isin(start_valid_h3)) & (od_matrix_first_50_59["end_h3"].isin(end_valid_h3)))
    mask_60_69 = ((od_matrix_first_60_69["start_h3"].isin(start_valid_h3)) & (od_matrix_first_60_69["end_h3"].isin(end_valid_h3)))
    mask_over70 = ((od_matrix_first_over70["start_h3"].isin(start_valid_h3)) & (od_matrix_first_over70["end_h3"].isin(end_valid_h3)))

    od_matrix_first_10_19 = od_matrix_first_10_19[mask_10_19].copy()
    od_matrix_first_20_29 = od_matrix_first_20_29[mask_20_29].copy()
    od_matrix_first_30_39 = od_matrix_first_30_39[mask_30_39].copy()
    od_matrix_first_40_49 = od_matrix_first_40_49[mask_40_49].copy()
    od_matrix_first_50_59 = od_matrix_first_50_59[mask_50_59].copy()
    od_matrix_first_60_69 = od_matrix_first_60_69[mask_60_69].copy()
    od_matrix_first_over70 = od_matrix_first_over70[mask_over70].copy()

elif mode == "PRO_CAT":
    mask_procat_1 = ((od_matrix_first_procat_1["start_h3"].isin(start_valid_h3)) & (od_matrix_first_procat_1["end_h3"].isin(end_valid_h3)))
    mask_procat_2 = ((od_matrix_first_procat_2["start_h3"].isin(start_valid_h3)) & (od_matrix_first_procat_2["end_h3"].isin(end_valid_h3)))
    mask_procat_3 = ((od_matrix_first_procat_3["start_h3"].isin(start_valid_h3)) & (od_matrix_first_procat_3["end_h3"].isin(end_valid_h3)))
    mask_procat_4 = ((od_matrix_first_procat_4["start_h3"].isin(start_valid_h3)) & (od_matrix_first_procat_4["end_h3"].isin(end_valid_h3)))
    mask_procat_5 = ((od_matrix_first_procat_5["start_h3"].isin(start_valid_h3)) & (od_matrix_first_procat_5["end_h3"].isin(end_valid_h3)))
    mask_procat_6 = ((od_matrix_first_procat_6["start_h3"].isin(start_valid_h3)) & (od_matrix_first_procat_6["end_h3"].isin(end_valid_h3)))
    mask_procat_7 = ((od_matrix_first_procat_7["start_h3"].isin(start_valid_h3)) & (od_matrix_first_procat_7["end_h3"].isin(end_valid_h3)))
    mask_procat_8 = ((od_matrix_first_procat_8["start_h3"].isin(start_valid_h3)) & (od_matrix_first_procat_8["end_h3"].isin(end_valid_h3)))

    od_matrix_first_procat_1 = od_matrix_first_procat_1[mask_procat_1].copy()
    od_matrix_first_procat_2 = od_matrix_first_procat_2[mask_procat_2].copy()
    od_matrix_first_procat_3 = od_matrix_first_procat_3[mask_procat_3].copy()
    od_matrix_first_procat_4 = od_matrix_first_procat_4[mask_procat_4].copy()
    od_matrix_first_procat_5 = od_matrix_first_procat_5[mask_procat_5].copy()
    od_matrix_first_procat_6 = od_matrix_first_procat_6[mask_procat_6].copy()
    od_matrix_first_procat_7 = od_matrix_first_procat_7[mask_procat_7].copy()
    od_matrix_first_procat_8 = od_matrix_first_procat_8[mask_procat_8].copy()

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")

In [32]:
if mode == "SEX":
    od_matrix_man = od_matrix_first_man.copy()
    od_matrix_woman = od_matrix_first_woman.copy()

elif mode == "AGE":
    od_matrix_10_19 = od_matrix_first_10_19.copy()
    od_matrix_20_29 = od_matrix_first_20_29.copy()
    od_matrix_30_39 = od_matrix_first_30_39.copy()
    od_matrix_40_49 = od_matrix_first_40_49.copy()
    od_matrix_50_59 = od_matrix_first_50_59.copy()
    od_matrix_60_69 = od_matrix_first_60_69.copy()
    od_matrix_over70 = od_matrix_first_over70.copy()

elif mode == "PRO_CAT":
    od_matrix_procat_1 = od_matrix_first_procat_1.copy()
    od_matrix_procat_2 = od_matrix_first_procat_2.copy()
    od_matrix_procat_3 = od_matrix_first_procat_3.copy()
    od_matrix_procat_4 = od_matrix_first_procat_4.copy()
    od_matrix_procat_5 = od_matrix_first_procat_5.copy()
    od_matrix_procat_6 = od_matrix_first_procat_6.copy()
    od_matrix_procat_7 = od_matrix_first_procat_7.copy()
    od_matrix_procat_8 = od_matrix_first_procat_8.copy()

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")

In [33]:
if mode == "SEX":
    filtered_df_man = df_merged.merge(od_matrix_man[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_woman = df_merged.merge(od_matrix_woman[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')

elif mode == "AGE":
    filtered_df_10_19 = df_merged.merge(od_matrix_10_19[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_20_29 = df_merged.merge(od_matrix_20_29[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_30_39 = df_merged.merge(od_matrix_30_39[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_40_49 = df_merged.merge(od_matrix_40_49[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_50_59 = df_merged.merge(od_matrix_50_59[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_60_69 = df_merged.merge(od_matrix_60_69[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_over70 = df_merged.merge(od_matrix_over70[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')

elif mode == "PRO_CAT":
    filtered_df_procat_1 = df_merged.merge(od_matrix_procat_1[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_procat_2 = df_merged.merge(od_matrix_procat_2[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_procat_3 = df_merged.merge(od_matrix_procat_3[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_procat_4 = df_merged.merge(od_matrix_procat_4[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_procat_5 = df_merged.merge(od_matrix_procat_5[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_procat_6 = df_merged.merge(od_matrix_procat_6[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_procat_7 = df_merged.merge(od_matrix_procat_7[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_procat_8 = df_merged.merge(od_matrix_procat_8[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")

In [34]:
class H3TreeNode:
    """Nodo dell'albero gerarchico H3"""
    def __init__(self, h3_id: str, resolution: int, total_weight: int = 0, count: int = 0):
        self.h3_id = h3_id
        self.resolution = resolution
        self.total_weight = total_weight
        self.count = count
        self.children: Dict[str, 'H3TreeNode'] = {}
        self.parent: Optional['H3TreeNode'] = None
    
    def add_child(self, child: 'H3TreeNode'):
        """Aggiunge un figlio al nodo"""
        self.children[child.h3_id] = child
        child.parent = self
    
    def add_weight(self, weight: int):
        self.total_weight += weight
        if self.parent:
            self.parent.add_weight(weight)
    
    def add_count(self, count: int):
        self.count += count
        if self.parent:
            self.parent.add_count(count)
    
    def __repr__(self):
        return (f"H3Node(id={self.h3_id}, res={self.resolution}, "
                f"total_weight={self.total_weight}, count={self.count}, children={len(self.children)})")

class H3HierarchicalTree:
    def __init__(self, od_matrix: pd.DataFrame, target_resolution: int = 11, hex_column: str = 'start_h3'):
        self.od_matrix = od_matrix
        self.target_resolution = target_resolution
        self.hex_column = hex_column  # 'start_h3' o 'end_h3'
        self.nodes: Dict[str, H3TreeNode] = {}
        self.root = None
        self.min_resolution = None  # Sarà calcolato dinamicamente
        
    def get_all_hexagons(self) -> Set[str]:
        """Estrae tutti gli esagoni unici dalla colonna specificata"""
        return set(self.od_matrix[self.hex_column].unique())
    
    def get_resolution_coverage(self, hexagons: Set[str], target_res: int) -> Set[str]:
        """
        Ottiene tutti gli esagoni di risoluzione target che coprono l'area
        definita dagli esagoni di input
        """
        coverage_hexagons = set()
        
        for hex_id in hexagons:
            current_res = h3.get_resolution(hex_id)
            
            if current_res == target_res:
                coverage_hexagons.add(hex_id)
            elif current_res < target_res:
                # Dobbiamo espandere a risoluzione più alta
                children = self._get_all_children_at_resolution(hex_id, target_res)
                coverage_hexagons.update(children)
            else:
                # Dobbiamo salire a risoluzione più bassa
                parent = h3.cell_to_parent(hex_id, target_res)
                coverage_hexagons.add(parent)
        
        return coverage_hexagons
    
    def find_optimal_min_resolution(self, hexagons: Set[str]) -> int:
        """
        Trova la risoluzione più alta dove c'è ancora un solo nodo che copre tutti gli esagoni
        """
        print("🔍 Analizzando risoluzione ottimale per radice...")
        
        # Per ogni risoluzione da 0 alla target, conta quanti nodi servono per coprire tutti gli esagoni
        resolution_stats = {}
        
        for resolution in range(0, self.target_resolution + 1):
            ancestors = set()
            for hex_id in hexagons:
                current_res = h3.get_resolution(hex_id)
                if current_res >= resolution:
                    ancestor = h3.cell_to_parent(hex_id, resolution)
                    ancestors.add(ancestor)
                else:
                    # L'esagono è già a risoluzione più bassa, aggiungi direttamente
                    ancestors.add(hex_id)
            
            resolution_stats[resolution] = len(ancestors)
            print(f"  - Risoluzione {resolution}: {len(ancestors)} nodi")
        
        # Trova la risoluzione più alta con count = 1
        optimal_resolution = 0
        for resolution in range(self.target_resolution, -1, -1):
            if resolution_stats[resolution] == 1:
                optimal_resolution = resolution
                break
        
        print(f"✅ Risoluzione ottimale trovata: {optimal_resolution}")
        return optimal_resolution
    
    def get_siblings(self, node_id: str) -> List[str]:
        """Restituisce gli h3_id dei nodi fratelli di node_id (stesso genitore, escluso node_id stesso)"""
        if node_id not in self.nodes:
            return []

        node = self.nodes[node_id]
        parent = node.parent
        if parent is None:
            # Nodo root, non ha fratelli
            return []

        siblings = [child.h3_id for child in parent.children.values() if child.h3_id != node_id]
        return siblings
    
    def get_parent(self, node_id: str) -> Optional[str]:
        """Restituisce l'h3_id del genitore del nodo dato, o None se root o nodo non trovato"""
        if node_id not in self.nodes:
            return None
        node = self.nodes[node_id]
        if node.parent is None:
            return None
        return node.parent.h3_id
    
    def _get_all_children_at_resolution(self, hex_id: str, target_res: int) -> Set[str]:
        """Ricorsivamente ottiene tutti i figli a una risoluzione specifica"""
        current_res = h3.get_resolution(hex_id)
        
        if current_res == target_res:
            return {hex_id}
        elif current_res > target_res:
            # Non dovrebbe succedere in questo contesto
            return set()
        
        children = set()
        direct_children = h3.cell_to_children(hex_id, current_res + 1)
        
        for child in direct_children:
            children.update(self._get_all_children_at_resolution(child, target_res))
        
        return children
    
    def build_hierarchy_path(self, hex_id: str, min_resolution: int) -> List[str]:
        """Costruisce il percorso gerarchico da un esagono fino alla risoluzione minima"""
        path = [hex_id]
        current = hex_id
        current_res = h3.get_resolution(current)
        
        while current_res > min_resolution:
            parent = h3.cell_to_parent(current, current_res - 1)
            path.append(parent)
            current = parent
            current_res -= 1
        
        return path
    
    def create_tree_structure(self):
        """Crea la struttura dell'albero ottimizzato"""
        target_hexagons = self.get_all_hexagons()
        
        # Ottieni copertura completa alla risoluzione target
        coverage_hexagons = self.get_resolution_coverage(target_hexagons, self.target_resolution)
        
        # Trova la risoluzione minima ottimale (quella più alta con count=1)
        self.min_resolution = self.find_optimal_min_resolution(coverage_hexagons)
        
        print(f"🏗️ Costruendo albero da risoluzione {self.min_resolution} a {self.target_resolution}")
        
        # Costruisci tutti i percorsi gerarchici
        all_paths = []
        for hex_id in coverage_hexagons:
            path = self.build_hierarchy_path(hex_id, self.min_resolution)
            all_paths.append(path)
        
        # Crea tutti i nodi
        for path in all_paths:
            for hex_id in path:
                if hex_id not in self.nodes:
                    resolution = h3.get_resolution(hex_id)
                    self.nodes[hex_id] = H3TreeNode(hex_id, resolution)
        
        # Stabilisci relazioni parent-child
        for path in all_paths:
            for i in range(len(path) - 1):
                child_id = path[i]
                parent_id = path[i + 1]
                self.nodes[parent_id].add_child(self.nodes[child_id])
        
        # Identifica la radice
        self.root = self.nodes[self._find_root_hexagon(coverage_hexagons, self.min_resolution)]
        
        return self
    
    def _find_root_hexagon(self, hexagons: Set[str], min_resolution: int) -> str:
        """Trova l'esagono radice che contiene tutti gli altri"""
        sample_hex = next(iter(hexagons))
        return h3.cell_to_parent(sample_hex, min_resolution)
    
    def populate_counts(self):
        # Raggruppa per esagono le due metriche
        agg_df = self.od_matrix.groupby(self.hex_column).agg({'total_weight': 'sum', 'count': 'sum'}).reset_index()
        
        for _, row in agg_df.iterrows():
            hex_id = row[self.hex_column]
            weight = int(row['total_weight'])
            count = int(row['count'])
            
            target_hex = self._map_to_target_resolution(hex_id)
            
            if target_hex in self.nodes:
                self.nodes[target_hex].add_weight(weight)
                self.nodes[target_hex].add_count(count)
            else:
                print(f"⚠️ Avviso: esagono {target_hex} non trovato nell'albero")
        
        return self
    
    def _map_to_target_resolution(self, hex_id: str) -> str:
        """Mappa un esagono alla risoluzione target"""
        current_res = h3.get_resolution(hex_id)
        
        if current_res == self.target_resolution:
            return hex_id
        elif current_res < self.target_resolution:
            # Prendi il primo figlio disponibile (potrebbe essere migliorato)
            children = self._get_all_children_at_resolution(hex_id, self.target_resolution)
            return next(iter(children)) if children else hex_id
        else:
            return h3.cell_to_parent(hex_id, self.target_resolution)
    
    def get_tree_statistics(self) -> Dict:
        """Ottiene statistiche dell'albero"""
        if not self.root:
            return {}
        
        stats = {
            'total_nodes': len(self.nodes),
            'root_resolution': self.root.resolution,
            'min_resolution': self.min_resolution,
            'target_resolution': self.target_resolution,
            'total_weight': self.root.total_weight,
            'nodes_by_resolution': defaultdict(int),
            'resolution_range': f"{self.min_resolution} → {self.target_resolution}"
        }
        
        for node in self.nodes.values():
            stats['nodes_by_resolution'][node.resolution] += 1
        
        return stats
    
    def print_tree(self, max_children_per_level: int = 10):
        if not self.root:
            print("❌ Albero non costruito")
            return
        
        print(f"\n🌳 STRUTTURA ALBERO OTTIMIZZATA")
        print(f"📏 Range risoluzione: {self.min_resolution} → {self.target_resolution}")
        print("=" * 80)
        
        def _print_node(node: H3TreeNode, depth: int = 0, is_last: bool = True, prefix: str = ""):
            connector = "└─ " if is_last else "├─ "
            print(f"{prefix}{connector}{node.h3_id} (res:{node.resolution}, total_weight:{node.total_weight}, count:{node.count}, children:{len(node.children)})")
            
            if is_last:
                child_prefix = prefix + "   "
            else:
                child_prefix = prefix + "│  "
            
            children_list = list(node.children.values())
            
            if len(children_list) <= max_children_per_level:
                for i, child in enumerate(children_list):
                    is_last_child = (i == len(children_list) - 1)
                    _print_node(child, depth + 1, is_last_child, child_prefix)
            else:
                for i in range(max_children_per_level):
                    child = children_list[i]
                    is_last_child = (i == max_children_per_level - 1) and (len(children_list) == max_children_per_level)
                    _print_node(child, depth + 1, is_last_child, child_prefix)
                
                remaining = len(children_list) - max_children_per_level
                print(f"{child_prefix}└─ ... e altri {remaining} figli con stesso pattern")
        
        _print_node(self.root, 0, True, "")

def create_h3_hierarchical_tree(od_matrix_df: pd.DataFrame, target_resolution: int = 10, hex_column: str = 'start_h3'):
    """
    Crea un albero gerarchico H3 ottimizzato dal dataset OD matrix
    
    Args:
        od_matrix_df: DataFrame con colonne 'start_h3', 'end_h3', 'count'
        target_resolution: Risoluzione target per le foglie dell'albero
        hex_column: Colonna da analizzare ('start_h3' o 'end_h3')
    
    Returns:
        H3HierarchicalTree: Albero gerarchico costruito e ottimizzato
    """
    
    tree = H3HierarchicalTree(od_matrix_df, target_resolution, hex_column)
    tree.create_tree_structure()
    tree.populate_counts()
    
    stats = tree.get_tree_statistics()
    print(f"\n📈 STATISTICHE ALBERO OTTIMIZZATO ({hex_column.upper()})")
    print("=" * 50)
    print(f"• Nodi totali: {stats['total_nodes']:,}")
    print(f"• Range risoluzione: {stats['resolution_range']}")
    print(f"• Risoluzione radice: {stats['root_resolution']}")
    print(f"• Risoluzione foglie: {stats['target_resolution']}")
    print(f"• Nodi per risoluzione:")
    for res in sorted(stats['nodes_by_resolution'].keys()):
        print(f"  - Risoluzione {res}: {stats['nodes_by_resolution'][res]:,} nodi")
    
    # Calcola risparmio in nodi
    total_resolutions_possible = target_resolution + 1  # da 0 a target
    resolutions_used = len(stats['nodes_by_resolution'])
    resolutions_saved = total_resolutions_possible - resolutions_used
    
    print(f"\n💡 OTTIMIZZAZIONI:")
    print(f"• Risoluzioni risparmiate: {resolutions_saved}")
    print(f"• Efficienza albero: {resolutions_used}/{total_resolutions_possible} livelli utilizzati")
    
    tree.print_tree()
    
    return tree

In [35]:
if mode == "SEX":
    tree_start_man = create_h3_hierarchical_tree(od_matrix_man, target_resolution=10, hex_column='start_h3')
    tree_start_woman = create_h3_hierarchical_tree(od_matrix_woman, target_resolution=10, hex_column='start_h3')

    tree_end_man = create_h3_hierarchical_tree(od_matrix_man, target_resolution=10, hex_column='end_h3')
    tree_end_woman = create_h3_hierarchical_tree(od_matrix_woman, target_resolution=10, hex_column='end_h3')

elif mode == "AGE":
    tree_start_10_19 = create_h3_hierarchical_tree(od_matrix_10_19, target_resolution=10, hex_column='start_h3')
    tree_start_20_29 = create_h3_hierarchical_tree(od_matrix_20_29, target_resolution=10, hex_column='start_h3')
    tree_start_30_39 = create_h3_hierarchical_tree(od_matrix_30_39, target_resolution=10, hex_column='start_h3')
    tree_start_40_49 = create_h3_hierarchical_tree(od_matrix_40_49, target_resolution=10, hex_column='start_h3')
    tree_start_50_59 = create_h3_hierarchical_tree(od_matrix_50_59, target_resolution=10, hex_column='start_h3')
    tree_start_60_69 = create_h3_hierarchical_tree(od_matrix_60_69, target_resolution=10, hex_column='start_h3')
    tree_start_over70 = create_h3_hierarchical_tree(od_matrix_over70, target_resolution=10, hex_column='start_h3')

    tree_end_10_19 = create_h3_hierarchical_tree(od_matrix_10_19, target_resolution=10, hex_column='end_h3')
    tree_end_20_29 = create_h3_hierarchical_tree(od_matrix_20_29, target_resolution=10, hex_column='end_h3')
    tree_end_30_39 = create_h3_hierarchical_tree(od_matrix_30_39, target_resolution=10, hex_column='end_h3')
    tree_end_40_49 = create_h3_hierarchical_tree(od_matrix_40_49, target_resolution=10, hex_column='end_h3')
    tree_end_50_59 = create_h3_hierarchical_tree(od_matrix_50_59, target_resolution=10, hex_column='end_h3')
    tree_end_60_69 = create_h3_hierarchical_tree(od_matrix_60_69, target_resolution=10, hex_column='end_h3')
    tree_end_over70 = create_h3_hierarchical_tree(od_matrix_over70, target_resolution=10, hex_column='end_h3')

elif mode == "PRO_CAT":
    tree_start_procat_1 = create_h3_hierarchical_tree(od_matrix_procat_1, target_resolution=10, hex_column='start_h3')
    tree_start_procat_2 = create_h3_hierarchical_tree(od_matrix_procat_2, target_resolution=10, hex_column='start_h3')
    tree_start_procat_3 = create_h3_hierarchical_tree(od_matrix_procat_3, target_resolution=10, hex_column='start_h3')
    tree_start_procat_4 = create_h3_hierarchical_tree(od_matrix_procat_4, target_resolution=10, hex_column='start_h3')
    tree_start_procat_5 = create_h3_hierarchical_tree(od_matrix_procat_5, target_resolution=10, hex_column='start_h3')
    tree_start_procat_6 = create_h3_hierarchical_tree(od_matrix_procat_6, target_resolution=10, hex_column='start_h3')
    tree_start_procat_7 = create_h3_hierarchical_tree(od_matrix_procat_7, target_resolution=10, hex_column='start_h3')
    tree_start_procat_8 = create_h3_hierarchical_tree(od_matrix_procat_8, target_resolution=10, hex_column='start_h3')

    tree_end_procat_1 = create_h3_hierarchical_tree(od_matrix_procat_1, target_resolution=10, hex_column='end_h3')
    tree_end_procat_2 = create_h3_hierarchical_tree(od_matrix_procat_2, target_resolution=10, hex_column='end_h3')
    tree_end_procat_3 = create_h3_hierarchical_tree(od_matrix_procat_3, target_resolution=10, hex_column='end_h3')
    tree_end_procat_4 = create_h3_hierarchical_tree(od_matrix_procat_4, target_resolution=10, hex_column='end_h3')
    tree_end_procat_5 = create_h3_hierarchical_tree(od_matrix_procat_5, target_resolution=10, hex_column='end_h3')
    tree_end_procat_6 = create_h3_hierarchical_tree(od_matrix_procat_6, target_resolution=10, hex_column='end_h3')
    tree_end_procat_7 = create_h3_hierarchical_tree(od_matrix_procat_7, target_resolution=10, hex_column='end_h3')
    tree_end_procat_8 = create_h3_hierarchical_tree(od_matrix_procat_8, target_resolution=10, hex_column='end_h3')

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")

🔍 Analizzando risoluzione ottimale per radice...
  - Risoluzione 0: 1 nodi
  - Risoluzione 1: 1 nodi
  - Risoluzione 2: 1 nodi
  - Risoluzione 3: 1 nodi
  - Risoluzione 4: 1 nodi
  - Risoluzione 5: 2 nodi
  - Risoluzione 6: 5 nodi
  - Risoluzione 7: 33 nodi
  - Risoluzione 8: 146 nodi
  - Risoluzione 9: 348 nodi
  - Risoluzione 10: 594 nodi
✅ Risoluzione ottimale trovata: 4
🏗️ Costruendo albero da risoluzione 4 a 10

📈 STATISTICHE ALBERO OTTIMIZZATO (START_H3)
• Nodi totali: 1,129
• Range risoluzione: 4 → 10
• Risoluzione radice: 4
• Risoluzione foglie: 10
• Nodi per risoluzione:
  - Risoluzione 4: 1 nodi
  - Risoluzione 5: 2 nodi
  - Risoluzione 6: 5 nodi
  - Risoluzione 7: 33 nodi
  - Risoluzione 8: 146 nodi
  - Risoluzione 9: 348 nodi
  - Risoluzione 10: 594 nodi

💡 OTTIMIZZAZIONI:
• Risoluzioni risparmiate: 4
• Efficienza albero: 7/11 livelli utilizzati

🌳 STRUTTURA ALBERO OTTIMIZZATA
📏 Range risoluzione: 4 → 10
└─ 841fb47ffffffff (res:4, total_weight:4529835, count:939, children:2

In [36]:
import numpy as np
import pandas as pd
import weakref
from math import *

class H3SbaAggregator:
    def __init__(self, od_matrix, tree_start, tree_end, param):
        # Copia e rinomina colonne
        self.od_matrix = od_matrix.copy()
        self.od_matrix = self.od_matrix.rename(columns={
            'start_h3': 'oi', 
            'end_h3': 'di', 
            'count': 'vol',
            'total_weight': 'weight'
        })
        
        self.tree_start = tree_start
        self.tree_end = tree_end
        self.param = param

        if param.get('target_vol_o') is None:
            raise ValueError('Must set a target_vol_o for tree aggregation')
        self.target_vol_o = param['target_vol_o']
        
        self.anon_thres = param['anon_thres']
        self.suppr_thres_frac = param['suppr_thres_frac']

        # Gestione dei timestep
        if 't' in self.od_matrix.columns:
            vol_ori_df = self.od_matrix.groupby('t')['vol'].sum().reset_index()
        else:
            self.od_matrix['t'] = 0
            vol_ori_df = pd.DataFrame({'t': [0], 'vol': [self.od_matrix['vol'].sum()]})

        self.eval_df = pd.DataFrame(columns=['t', 'vol_ori', 'vol_kept', 'nb_flows'])
        self.od_matrix_agg = pd.DataFrame(columns=['coi', 'cdi', 'vol', 'weight', 't', 'censored'])
        self.od_matrix_agg['censored'] = self.od_matrix_agg['censored'].astype(bool)

        for _, vol_ori_row in vol_ori_df.iterrows():
            timestep = vol_ori_row['t']
            od_matrix_agg_timestep = self.solve_timestep(timestep)

            total_vol = od_matrix_agg_timestep['vol'].sum()
            if total_vol != vol_ori_row['vol']:
                if total_vol >= self.anon_thres:
                    print(f"Warning: missing some volumes! ({od_matrix_agg_timestep['vol'].sum()} vs {vol_ori_row['vol']})")
                else:
                    print('Censored everything as total volume < anon thres')

            self.od_matrix_agg = pd.concat([self.od_matrix_agg, od_matrix_agg_timestep])

            eval_row = {
                't': timestep,
                'vol_ori': vol_ori_row['vol'],
                'vol_kept': (od_matrix_agg_timestep['vol']*(~od_matrix_agg_timestep['censored'])).sum(),
                'nb_flows': len(self.od_matrix_timestep),
            }
            self.eval_df = pd.concat([self.eval_df, pd.DataFrame(eval_row, index=[len(self.eval_df)])])

    def solve_timestep(self, timestep):
        ori_df = self.get_ori_df(timestep)
        total_vol = ori_df.sum()
        
        if total_vol < self.anon_thres:
            return pd.DataFrame({'coi': [self.tree_start.root.h3_id],
                                 'cdi': [self.tree_end.root.h3_id],
                                 'vol': 0,
                                 'weight': 0,
                                 't': timestep,
                                 'censored': total_vol != 0})
        elif total_vol == self.anon_thres:
            return pd.DataFrame({'coi': [self.tree_start.root.h3_id],
                                 'cdi': [self.tree_end.root.h3_id],
                                 'vol': total_vol,
                                 'weight': self.od_matrix_timestep['weight'].sum(),
                                 't': timestep,
                                 'censored': False})
        
        qo = H3VQuadtree(pop_df=ori_df,
                         h3_root=self.tree_start.root,
                         target_vol=self.target_vol_o,
                         ci_col='oi', vol_col='vol')
        o_partition = qo.flat_leaves

        od_matrix_agg_timestep = self.get_dest_agg(o_partition)
        od_matrix_agg_timestep['t'] = timestep
        od_matrix_agg_timestep['censored'] = (od_matrix_agg_timestep['vol'] < self.param['anon_thres']) & (od_matrix_agg_timestep['vol'] != 0)

        return od_matrix_agg_timestep

    def get_dest_agg(self, clusters_o):
        dest_df = self.get_dest_df(clusters_o)

        tree = H3SbaTree(pop_df=dest_df,
                         h3_root=self.tree_end.root,
                         clusters_o=clusters_o,
                         anon_thres=self.anon_thres)

        OD_report = tree.sba_solve(self.suppr_thres_frac * sum([co.vol for co in clusters_o]))
        od_matrix_agg_timestep = pd.DataFrame(OD_report, columns=['coi', 'cdi', 'vol', 'weight'])

        return od_matrix_agg_timestep

    def get_ori_df(self, timestep):
        self.od_matrix_timestep = self.od_matrix[self.od_matrix['t'] == timestep]
        ori_df = self.od_matrix_timestep.groupby('oi')['vol'].sum()
        return ori_df

    def get_dest_df(self, clusters_o):
        nb_leaves_by_cluster_o = [len(cluster_o.flat_leaves_name) for cluster_o in clusters_o]
        oicoidf = pd.DataFrame({
             'oi': np.concatenate([cluster_o.flat_leaves_name for cluster_o in clusters_o]),
             'coi': np.repeat([cluster_o.h3_node.h3_id for cluster_o in clusters_o], nb_leaves_by_cluster_o)
        })

        dest_df = self.od_matrix_timestep.merge(oicoidf, on='oi', how='outer').drop(columns=['oi'])
        dest_df = dest_df.groupby(['coi', 'di']).agg({'vol': 'sum', 'weight': 'sum'}).reset_index()
        dest_df = dest_df.groupby('di').agg(list)

        return dest_df


class H3SbaTree:
    def __init__(self, pop_df, h3_root, clusters_o, anon_thres=0):
        self.pop_df = pop_df
        self.anon_thres = anon_thres
        
        self.clusters_o = clusters_o
        self.cluster_order = {cluster.h3_node.h3_id: i for i, cluster in enumerate(clusters_o)}
        
        self.area = h3_root.resolution
        self.areas_o = np.array([co.h3_node.resolution for co in self.clusters_o])
        
        self.root = H3SbaNode(h3_root, weakref.ref(self))

    def sba_solve(self, S):
        left_delta = 0
        self.root.activate(left_delta)
        left_slope = self.root.best_vol_suppr.sum() - S
        left_score = self.root.best_score.sum() - left_delta*S
        if left_slope < 0:
            return self.get_leaves_arr()

        right_delta = self.area
        self.root.activate(right_delta)
        right_slope = self.root.best_vol_suppr.sum() - S
        right_score = self.root.best_score.sum() - right_delta*S
        
        while right_slope > 0:
            left_delta = right_delta
            left_slope = right_slope
            left_score = right_score
            right_delta += self.area
            self.root.activate(right_delta)
            right_slope = self.root.best_vol_suppr.sum() - S
            right_score = self.root.best_score.sum() - right_delta*S
        
        while True:
            mid_delta = (left_slope*left_delta - right_slope*right_delta + right_score - left_score)/(left_slope - right_slope)
            self.root.activate(mid_delta)
            mid_slope = self.root.best_vol_suppr.sum() - S
            mid_score = self.root.best_score.sum() - mid_delta*S
            
            if round(mid_delta-left_delta, 5) == 0 or round(mid_delta-right_delta, 5) == 0:
                return self.get_leaves_arr()
            else:
                if mid_slope > 0:
                    left_delta = mid_delta
                    left_slope = mid_slope
                    left_score = mid_score
                else:
                    right_delta = mid_delta
                    right_slope = mid_slope
                    right_score = mid_score

    def get_leaves_arr(self):
        leaves_arr = []
        for ori_counter in range(len(self.cluster_order)):
            self.root.get_leaves_arr_rec(leaves_arr, ori_counter)
        return leaves_arr


class H3SbaNode:
    def __init__(self, h3_tree_node, tree_weakref, parent=None):
        self.tree_weakref = tree_weakref
        self.h3_node = h3_tree_node
        self.k = self.tree_weakref().anon_thres
        
        self.children = [H3SbaNode(child, tree_weakref, self) for child in h3_tree_node.children.values()]
        cluster_order = self.tree_weakref().cluster_order
        self.vol_raw = np.zeros(len(cluster_order))
        self.weight_raw = np.zeros(len(cluster_order))
        
        if len(self.children) == 0:
            row = None
            try:
                row = self.tree_weakref().pop_df.loc[self.h3_node.h3_id]
            except KeyError:
                pass
            if row is not None:
                vols = row['vol']
                weights = row['weight']
                cois = row['coi']
                for i in range(len(cois)):
                    self.vol_raw[cluster_order[cois[i]]] = vols[i]
                    self.weight_raw[cluster_order[cois[i]]] = weights[i]
        elif len(self.children) > 0:
            self.vol_raw = np.sum([c.vol_raw for c in self.children], axis=0)
            self.weight_raw = np.sum([c.weight_raw for c in self.children], axis=0)
        
        self.censored = (self.vol_raw > 0) & (self.vol_raw < self.k)
        self.agg_vol_suppr = self.vol_raw * self.censored
        
        self.area = self.h3_node.resolution
        self.agg_error = self.vol_raw * (~self.censored) * (self.tree_weakref().areas_o + self.area)

    def activate(self, delta):
        for c in self.children:
            c.activate(delta)

        self.split_this = np.zeros(len(self.tree_weakref().clusters_o), dtype=bool)
        self.best_vol_suppr = self.agg_vol_suppr.copy()
        self.best_score = self.agg_error + self.agg_vol_suppr * delta

        if len(self.children) > 0:
            split_score = np.sum([c.best_score for c in self.children], axis=0)
            split_mask = (split_score < self.best_score) & (self.vol_raw > self.k)
            self.split_this[split_mask] = True
            self.best_score[split_mask] = split_score[split_mask]
            split_vol_suppr = np.sum([c.best_vol_suppr for c in self.children], axis=0)
            self.best_vol_suppr[split_mask] = split_vol_suppr[split_mask]

    def summary(self, ori_counter):
        cluster_h3_id = self.tree_weakref().clusters_o[ori_counter].h3_node.h3_id
        return [cluster_h3_id, self.h3_node.h3_id, self.vol_raw[ori_counter], self.weight_raw[ori_counter]]

    def get_leaves_arr_rec(self, leaves_arr, ori_counter):
        if not self.split_this[ori_counter]:
            leaves_arr += [self.summary(ori_counter)]
        else:
            for c in self.children:
                c.get_leaves_arr_rec(leaves_arr, ori_counter)


class H3VQuadtree:
    def __init__(self, pop_df, h3_root, target_vol, ci_col, vol_col):
        self.h3_root = h3_root
        self.pop_df = pop_df
        self.target_vol = target_vol
        self.flat_leaves = []
        self.ci_col = ci_col
        self.vol_col = vol_col
        self.grow()

    def grow(self):
        self.root = H3VQuadNode(self.h3_root, self)
        self.root.compute_best_split()
        self.root.keep_subtree(keep_condition=lambda x: x.split_this)
        self.flat_leaves = self.flatten_leaves()

    def flatten_leaves(self):
        flat_leaves = []
        self.root.flatten_leaves_rec(flat_leaves)
        return flat_leaves

    def get_total_error(self):
        return sum([leaf.error for leaf in self.flat_leaves])


class H3VQuadNode:
    def __init__(self, h3_tree_node, tree):
        self.tree = tree
        self.h3_node = h3_tree_node
        self.children = [H3VQuadNode(child, tree) for child in h3_tree_node.children.values()]
        if len(self.children) == 0:
            try:
                self.vol = self.tree.pop_df.loc[self.h3_node.h3_id]
            except KeyError:
                self.vol = 0
        else:
            self.vol = sum([c.vol for c in self.children])
        self.h3_node.vol = self.vol
        if len(self.children) == 0:
            self.flat_leaves_name = [self.h3_node.h3_id]
        else:
            self.flat_leaves_name = []
            for child in self.children:
                self.flat_leaves_name.extend(child.flat_leaves_name)
        self.error = self.compute_error()

    def compute_error(self):
        if self.vol == 0:
            return 0
        return (self.tree.target_vol - self.vol)**2

    def keep_subtree(self, keep_condition):
        if keep_condition(self):
            for c in self.children:
                c.keep_subtree(keep_condition)
        else:
            self.children = []

    def compute_best_split(self):
        self.split_this = False
        self.best_score = self.error
        if self.vol > 0:
            if len(self.children) == 0:
                self.split_this = False
            else:
                for c in self.children:
                    c.compute_best_split()
                split_score = sum([c.best_score for c in self.children])
                if split_score <= self.error:
                    self.split_this = True
                    self.best_score = split_score

    def flatten_leaves_rec(self, flat_leaves):
        if len(self.children) == 0:
            flat_leaves += [self]
        else:
            for c in self.children:
                c.flatten_leaves_rec(flat_leaves)

In [37]:
if mode == "SEX":
    print("\n--- CREAZIONE AGGREGATORI SEX ---")
    
    print("Man:")
    param_man = {
        'anon_thres': 10,
        'suppr_thres_frac': 0.1,
        'target_vol_o': 1000,
    }
    aggregator_man = H3SbaAggregator(
        od_matrix=od_matrix_man,
        tree_start=tree_start_man,
        tree_end=tree_end_man,
        param=param_man
    )
    
    print("Woman:")
    param_woman = {
        'anon_thres': 10,
        'suppr_thres_frac': 0.1,
        'target_vol_o': 1350,
    }
    aggregator_woman = H3SbaAggregator(
        od_matrix=od_matrix_woman,
        tree_start=tree_start_woman,
        tree_end=tree_end_woman,
        param=param_woman
    )

elif mode == "AGE":
    print("\n--- CREAZIONE AGGREGATORI AGE ---")
    aggregators_age = {}
    for label in ["10_19", "20_29", "30_39", "40_49", "50_59", "60_69", "over70"]:
        print(f"Creazione aggregatore per {label}")
        od_matrix_label = globals()[f"od_matrix_{label}"]
        tree_start_label = globals()[f"tree_start_{label}"]
        tree_end_label = globals()[f"tree_end_{label}"]
        param_label = {
            'anon_thres': 10,
            'suppr_thres_frac': 0.1,
            'target_vol_o': 1000  # eventualmente personalizzabile per fascia
        }
        aggregators_age[label] = H3SbaAggregator(
            od_matrix=od_matrix_label,
            tree_start=tree_start_label,
            tree_end=tree_end_label,
            param=param_label
        )

elif mode == "PRO_CAT":
    print("\n--- CREAZIONE AGGREGATORI PRO_CAT ---")
    aggregators_procat = {}
    for i in range(1, 9):
        print(f"Creazione aggregatore ProCat-{i}")
        od_matrix_label = globals()[f"od_matrix_procat_{i}"]
        tree_start_label = globals()[f"tree_start_procat_{i}"]
        tree_end_label = globals()[f"tree_end_procat_{i}"]
        param_label = {
            'anon_thres': 10,
            'suppr_thres_frac': 0.1,
            'target_vol_o': 1000  # eventualmente personalizzabile
        }
        aggregators_procat[f"ProCat-{i}"] = H3SbaAggregator(
            od_matrix=od_matrix_label,
            tree_start=tree_start_label,
            tree_end=tree_end_label,
            param=param_label
        )

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")



--- CREAZIONE AGGREGATORI AGE ---
Creazione aggregatore per 10_19
Creazione aggregatore per 20_29


C:\Users\dmc\AppData\Local\Temp\ipykernel_5376\64128813.py:50: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  self.od_matrix_agg = pd.concat([self.od_matrix_agg, od_matrix_agg_timestep])
C:\Users\dmc\AppData\Local\Temp\ipykernel_5376\64128813.py:58: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  self.eval_df = pd.concat([self.eval_df, pd.DataFrame(eval_row, index=[len(self.eval_df)])])
C:\Users\dmc\AppData\Local\Temp\ipykernel_5376\64128813.py:50: FutureWarning: The behavior of DataFrame concatena

Creazione aggregatore per 30_39


C:\Users\dmc\AppData\Local\Temp\ipykernel_5376\64128813.py:50: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  self.od_matrix_agg = pd.concat([self.od_matrix_agg, od_matrix_agg_timestep])
C:\Users\dmc\AppData\Local\Temp\ipykernel_5376\64128813.py:58: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  self.eval_df = pd.concat([self.eval_df, pd.DataFrame(eval_row, index=[len(self.eval_df)])])


Creazione aggregatore per 40_49


C:\Users\dmc\AppData\Local\Temp\ipykernel_5376\64128813.py:50: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  self.od_matrix_agg = pd.concat([self.od_matrix_agg, od_matrix_agg_timestep])
C:\Users\dmc\AppData\Local\Temp\ipykernel_5376\64128813.py:58: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  self.eval_df = pd.concat([self.eval_df, pd.DataFrame(eval_row, index=[len(self.eval_df)])])


Creazione aggregatore per 50_59


C:\Users\dmc\AppData\Local\Temp\ipykernel_5376\64128813.py:50: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  self.od_matrix_agg = pd.concat([self.od_matrix_agg, od_matrix_agg_timestep])
C:\Users\dmc\AppData\Local\Temp\ipykernel_5376\64128813.py:58: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  self.eval_df = pd.concat([self.eval_df, pd.DataFrame(eval_row, index=[len(self.eval_df)])])


Creazione aggregatore per 60_69
Creazione aggregatore per over70


C:\Users\dmc\AppData\Local\Temp\ipykernel_5376\64128813.py:50: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  self.od_matrix_agg = pd.concat([self.od_matrix_agg, od_matrix_agg_timestep])
C:\Users\dmc\AppData\Local\Temp\ipykernel_5376\64128813.py:58: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  self.eval_df = pd.concat([self.eval_df, pd.DataFrame(eval_row, index=[len(self.eval_df)])])
C:\Users\dmc\AppData\Local\Temp\ipykernel_5376\64128813.py:50: FutureWarning: The behavior of DataFrame concatena

In [38]:
if mode == "SEX":
    print("\n--- ESTRAZIONE MATRICE AGGREGATA SEX ---")
    
    print("Man:")
    od_matrix_agg_man = aggregator_man.od_matrix_agg
    
    print("Woman:")
    od_matrix_agg_woman = aggregator_woman.od_matrix_agg

elif mode == "AGE":
    print("\n--- ESTRAZIONE MATRICE AGGREGATA AGE ---")
    od_matrix_agg_age = {}
    for label in ["10_19", "20_29", "30_39", "40_49", "50_59", "60_69", "over70"]:
        print(f"Estrazione matrice aggregata per {label}")
        od_matrix_agg_age[label] = aggregators_age[label].od_matrix_agg

elif mode == "PRO_CAT":
    print("\n--- ESTRAZIONE MATRICE AGGREGATA PRO_CAT ---")
    od_matrix_agg_procat = {}
    for i in range(1, 9):
        print(f"Estrazione matrice aggregata per ProCat-{i}")
        od_matrix_agg_procat[f"ProCat-{i}"] = aggregators_procat[f"ProCat-{i}"].od_matrix_agg

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")



--- ESTRAZIONE MATRICE AGGREGATA AGE ---
Estrazione matrice aggregata per 10_19
Estrazione matrice aggregata per 20_29
Estrazione matrice aggregata per 30_39
Estrazione matrice aggregata per 40_49
Estrazione matrice aggregata per 50_59
Estrazione matrice aggregata per 60_69
Estrazione matrice aggregata per over70


In [39]:
if mode == "SEX":
    print("\n--- CALCOLO VOLUME SOPPRESSO SEX ---")
    
    print("Man:")
    suppressed_count_man = od_matrix_agg_man[od_matrix_agg_man["censored"] == True]["vol"].sum()
    print(f"Totale volume soppresso (Man): {suppressed_count_man:,}")
    
    print("Woman:")
    suppressed_count_woman = od_matrix_agg_woman[od_matrix_agg_woman["censored"] == True]["vol"].sum()
    print(f"Totale volume soppresso (Woman): {suppressed_count_woman:,}")

elif mode == "AGE":
    print("\n--- CALCOLO VOLUME SOPPRESSO AGE ---")
    suppressed_count_age = {}
    for label in ["10_19", "20_29", "30_39", "40_49", "50_59", "60_69", "over70"]:
        suppressed_count_age[label] = aggregators_age[label].od_matrix_agg[
            aggregators_age[label].od_matrix_agg["censored"] == True
        ]["vol"].sum()
        print(f"Totale volume soppresso ({label}): {suppressed_count_age[label]:,}")

elif mode == "PRO_CAT":
    print("\n--- CALCOLO VOLUME SOPPRESSO PRO_CAT ---")
    suppressed_count_procat = {}
    for i in range(1, 9):
        key = f"ProCat-{i}"
        suppressed_count_procat[key] = aggregators_procat[key].od_matrix_agg[
            aggregators_procat[key].od_matrix_agg["censored"] == True
        ]["vol"].sum()
        print(f"Totale volume soppresso ({key}): {suppressed_count_procat[key]:,}")

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")



--- CALCOLO VOLUME SOPPRESSO AGE ---
Totale volume soppresso (10_19): 0.0
Totale volume soppresso (20_29): 0.0
Totale volume soppresso (30_39): 0.0
Totale volume soppresso (40_49): 642.0
Totale volume soppresso (50_59): 0.0
Totale volume soppresso (60_69): 1,279.0
Totale volume soppresso (over70): 0.0


In [40]:
if mode == "SEX":
    print("\n--- PULIZIA E RINOMINA OD_MATRIX SEX ---")
    
    print("Man:")
    od_matrix_agg_man = od_matrix_agg_man[od_matrix_agg_man["censored"] == False]
    od_matrix_agg_man = od_matrix_agg_man.rename(columns={
        "coi": "start_h3",
        "cdi": "end_h3",
        "vol": "count"
    })
    od_matrix_agg_man = od_matrix_agg_man.drop(columns=["t", "censored"], errors="ignore")
    od_matrix_agg_man = od_matrix_agg_man[od_matrix_agg_man['count'] > 0.0]
    print(f"Righe finali Man: {len(od_matrix_agg_man):,}")

    print("Woman:")
    od_matrix_agg_woman = od_matrix_agg_woman[od_matrix_agg_woman["censored"] == False]
    od_matrix_agg_woman = od_matrix_agg_woman.rename(columns={
        "coi": "start_h3",
        "cdi": "end_h3",
        "vol": "count"
    })
    od_matrix_agg_woman = od_matrix_agg_woman.drop(columns=["t", "censored"], errors="ignore")
    od_matrix_agg_woman = od_matrix_agg_woman[od_matrix_agg_woman['count'] > 0.0]
    print(f"Righe finali Woman: {len(od_matrix_agg_woman):,}")

elif mode == "AGE":
    print("\n--- PULIZIA E RINOMINA OD_MATRIX AGE ---")
    od_matrix_agg_age_clean = {}
    for label in ["10_19", "20_29", "30_39", "40_49", "50_59", "60_69", "over70"]:
        print(f"Pulizia {label}:")
        df = aggregators_age[label].od_matrix_agg
        df = df[df["censored"] == False]
        df = df.rename(columns={"coi": "start_h3", "cdi": "end_h3", "vol": "count"})
        df = df.drop(columns=["t", "censored"], errors="ignore")
        df = df[df['count'] > 0.0]
        od_matrix_agg_age_clean[label] = df
        print(f"  Righe finali {label}: {len(df):,}")

elif mode == "PRO_CAT":
    print("\n--- PULIZIA E RINOMINA OD_MATRIX PRO_CAT ---")
    od_matrix_agg_procat_clean = {}
    for i in range(1, 9):
        key = f"ProCat-{i}"
        print(f"Pulizia {key}:")
        df = aggregators_procat[key].od_matrix_agg
        df = df[df["censored"] == False]
        df = df.rename(columns={"coi": "start_h3", "cdi": "end_h3", "vol": "count"})
        df = df.drop(columns=["t", "censored"], errors="ignore")
        df = df[df['count'] > 0.0]
        od_matrix_agg_procat_clean[key] = df
        print(f"  Righe finali {key}: {len(df):,}")

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")



--- PULIZIA E RINOMINA OD_MATRIX AGE ---
Pulizia 10_19:
  Righe finali 10_19: 1
Pulizia 20_29:
  Righe finali 20_29: 5
Pulizia 30_39:
  Righe finali 30_39: 5
Pulizia 40_49:
  Righe finali 40_49: 8
Pulizia 50_59:
  Righe finali 50_59: 5
Pulizia 60_69:
  Righe finali 60_69: 11
Pulizia over70:
  Righe finali over70: 1


In [41]:
import folium
import h3
import pandas as pd

class GeneralizedH3Visualizer:
    def __init__(self, od_matrix, center_lat=48.8566, center_lon=2.3522):
        """
        Visualizza una OD matrix generalizzata H3 su Folium.

        Args:
            od_matrix: DataFrame con colonne ['start_h3', 'end_h3', 'count']
            center_lat, center_lon: coordinate del centro della mappa
        """
        self.od_matrix = od_matrix
        self.center_lat = center_lat
        self.center_lon = center_lon
        
        # Totali per origine e destinazione
        self.origin_flows = od_matrix.groupby('start_h3')['count'].sum().to_dict()
        self.dest_flows = od_matrix.groupby('end_h3')['count'].sum().to_dict()
    
    def _h3_to_geojson(self, h3_id):
        """Converte un esagono H3 in GeoJSON"""
        boundary = h3.cell_to_boundary(h3_id)
        coords = [[[lon, lat] for lat, lon in boundary]]  # GeoJSON vuole lon, lat
        return {
            "type": "Feature",
            "geometry": {"type": "Polygon", "coordinates": coords},
            "properties": {"h3_id": h3_id, "resolution": h3.get_resolution(h3_id)}
        }
    
    def create_map(self, max_hexagons=100, alpha=0.6, zoom_start=10):
        """Crea la mappa Folium con esagoni di origine e destinazione"""
        m = folium.Map(location=[self.center_lat, self.center_lon], zoom_start=zoom_start, tiles='OpenStreetMap')
        
        # Layer Origini (blu)
        origins_sorted = sorted(self.origin_flows.items(), key=lambda x: x[1], reverse=True)[:max_hexagons]
        origin_layer = folium.FeatureGroup(name="Origini (blu)", show=True)
        if origins_sorted:
            min_flow, max_flow = min(v for _, v in origins_sorted), max(v for _, v in origins_sorted)
            for h3_id, count in origins_sorted:
                geojson = self._h3_to_geojson(h3_id)
                intensity = (count - min_flow) / (max_flow - min_flow) if max_flow > min_flow else 1.0
                blue_intensity = int(255 * (0.3 + 0.7*intensity))
                fill_color = f"#{0:02x}{0:02x}{blue_intensity:02x}"
                folium.GeoJson(
                    geojson,
                    style_function=lambda x, fill_color=fill_color: {
                        'fillColor': fill_color,
                        'color': 'darkblue',
                        'weight': 1,
                        'fillOpacity': alpha,
                        'opacity': 0.8
                    },
                    tooltip=f"{count} viaggi"
                ).add_to(origin_layer)
        origin_layer.add_to(m)
        
        # Layer Destinazioni (rosso)
        dest_sorted = sorted(self.dest_flows.items(), key=lambda x: x[1], reverse=True)[:max_hexagons]
        dest_layer = folium.FeatureGroup(name="Destinazioni (rosso)", show=True)
        if dest_sorted:
            min_flow, max_flow = min(v for _, v in dest_sorted), max(v for _, v in dest_sorted)
            for h3_id, count in dest_sorted:
                geojson = self._h3_to_geojson(h3_id)
                intensity = (count - min_flow) / (max_flow - min_flow) if max_flow > min_flow else 1.0
                red_intensity = int(255 * (0.3 + 0.7*intensity))
                fill_color = f"#{red_intensity:02x}{0:02x}{0:02x}"
                folium.GeoJson(
                    geojson,
                    style_function=lambda x, fill_color=fill_color: {
                        'fillColor': fill_color,
                        'color': 'darkred',
                        'weight': 1,
                        'fillOpacity': alpha,
                        'opacity': 0.8
                    },
                    tooltip=f"{count} viaggi"
                ).add_to(dest_layer)
        dest_layer.add_to(m)
        
        folium.LayerControl().add_to(m)

        # Aggiungi legenda HTML con numero di esagoni
        legend_html = f"""
        <div style="
            position: fixed; 
            bottom: 30px; left: 30px; width: 220px; height: 80px; 
            background-color: white;
            border:2px solid grey; z-index:9999; font-size:14px;
            padding: 10px;
        ">
        <b>Legenda esagoni</b><br>
        <span style="color:darkblue;">&#9632;</span> Origini: {len(origins_sorted)}<br>
        <span style="color:darkred;">&#9632;</span> Destinazioni: {len(dest_sorted)}
        </div>
        """
        m.get_root().html.add_child(folium.Element(legend_html))

        return m


In [42]:
if mode == "SEX":
    print("\n--- VISUALIZZAZIONE OD_MATRIX SEX ---")
    
    print("Mappa Uomini:")
    visualizer_man = GeneralizedH3Visualizer(od_matrix_agg_man)
    mappa_man = visualizer_man.create_map(max_hexagons=2000000)
    display(mappa_man)
    
    print("Mappa Donne:")
    visualizer_woman = GeneralizedH3Visualizer(od_matrix_agg_woman)
    mappa_woman = visualizer_woman.create_map(max_hexagons=2000000)
    display(mappa_woman)

elif mode == "AGE":
    print("\n--- VISUALIZZAZIONE OD_MATRIX AGE ---")
    for label in ["10_19", "20_29", "30_39", "40_49", "50_59", "60_69", "over70"]:
        print(f"Mappa {label}:")
        visualizer = GeneralizedH3Visualizer(od_matrix_agg_age_clean[label])
        mappa = visualizer.create_map(max_hexagons=2000000)
        display(mappa)

elif mode == "PRO_CAT":
    print("\n--- VISUALIZZAZIONE OD_MATRIX PRO_CAT ---")
    for i in range(1, 9):
        key = f"ProCat-{i}"
        print(f"Mappa {key}:")
        visualizer = GeneralizedH3Visualizer(od_matrix_agg_procat_clean[key])
        mappa = visualizer.create_map(max_hexagons=2000000)
        display(mappa)

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")



--- VISUALIZZAZIONE OD_MATRIX AGE ---
Mappa 10_19:


Mappa 20_29:


Mappa 30_39:


Mappa 40_49:


Mappa 50_59:


Mappa 60_69:


Mappa over70:


In [43]:
import numpy as np
import pandas as pd

def compute_discernability_and_cavg(df: pd.DataFrame, k: int, suppressed_count: int = 0) -> dict:
    """
    Calcola C_DM e C_AVG per un dataset OD generalizzato.
    
    Args:
        df: DataFrame con colonne ['start_h3', 'end_h3', 'count']
        k: soglia k-anonimity
        suppressed_count: numero di coppie OD soppressi (facoltativo)
    
    Returns:
        dict con C_DM, C_AVG, numero totale record e classi equivalenza
    """
    counts = df['count'].values
    total_records = counts.sum() + suppressed_count
    total_equiv_classes = len(counts) + suppressed_count
    total_records_avg = counts.sum()
    total_equiv_classes_avg = len(counts)
    
    # C_DM: somma dei quadrati dei count >= k
    k_anonymous_counts = counts[counts >= k]
    c_dm_gen = np.sum(k_anonymous_counts**2)
    
    # Penalità per record soppressi
    suppression_penalty = suppressed_count * counts.sum()  # o totale record, a seconda della definizione
    c_dm = c_dm_gen + suppression_penalty
    
    # C_AVG: (total_records / total_equiv_classes) / k
    c_avg = (total_records_avg / total_equiv_classes_avg) / k if total_equiv_classes_avg > 0 else float('inf')
    
    return {
        'C_DM': c_dm,
        'C_AVG': c_avg,
        'total_records': total_records,
        'total_equivalence_classes': total_equiv_classes,
        'k': k
    }

if mode == "SEX":
    print("\n--- METRICHE DISCERNIBILITÀ SEX ---")
    
    metrics_man = compute_discernability_and_cavg(od_matrix_agg_man, suppressed_count=suppressed_count_man, k=10)
    print("Man:")
    print(f"   C_DM: {metrics_man['C_DM']:,} | C_AVG: {metrics_man['C_AVG']:.4f}")
    
    metrics_woman = compute_discernability_and_cavg(od_matrix_agg_woman, suppressed_count=suppressed_count_woman, k=10)
    print("Woman:")
    print(f"   C_DM: {metrics_woman['C_DM']:,} | C_AVG: {metrics_woman['C_AVG']:.4f}")

elif mode == "AGE":
    print("\n--- METRICHE DISCERNIBILITÀ AGE ---")
    age_labels = ["10_19", "20_29", "30_39", "40_49", "50_59", "60_69", "over70"]
    for label in age_labels:
        metrics = compute_discernability_and_cavg(od_matrix_agg_age_clean[label], suppressed_count=suppressed_count_age[label], k=10)
        print(f"{label}: C_DM: {metrics['C_DM']:,} | C_AVG: {metrics['C_AVG']:.4f}")

elif mode == "PRO_CAT":
    print("\n--- METRICHE DISCERNIBILITÀ PRO_CAT ---")
    for i in range(1, 9):
        key = f"ProCat-{i}"
        metrics = compute_discernability_and_cavg(od_matrix_agg_procat_clean[key], suppressed_count=suppressed_count_procat[key], k=10)
        print(f"{key}: C_DM: {metrics['C_DM']:,} | C_AVG: {metrics['C_AVG']:.4f}")

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")


--- METRICHE DISCERNIBILITÀ AGE ---
10_19: C_DM: 881,721.0 | C_AVG: 93.9000
20_29: C_DM: 11,196,151.0 | C_AVG: 137.6200
30_39: C_DM: 7,678,914.0 | C_AVG: 113.0000
40_49: C_DM: 10,678,836.0 | C_AVG: 65.4000
50_59: C_DM: 5,067,064.0 | C_AVG: 93.0400
60_69: C_DM: 3,355,244.0 | C_AVG: 16.1545
over70: C_DM: 1,324,801.0 | C_AVG: 115.1000


In [44]:
from geopy.distance import geodesic

def calculate_generalization_distance_metric(df: pd.DataFrame, od_matrix_generalized: pd.DataFrame) -> Dict:
   
   print("🔍 Calcolo metrica di distanza post-generalizzazione...")
   
   # 1. Crea mapping da esagoni originali a esagoni generalizzati
   start_original_to_generalized = {}
   end_original_to_generalized = {}
   
   # Ottieni tutti gli esagoni generalizzati unici
   generalized_start_h3 = set(od_matrix_generalized['start_h3'].unique())
   generalized_end_h3 = set(od_matrix_generalized['end_h3'].unique())
   
   # Per ogni esagono originale, trova l'esagono generalizzato corrispondente
   unique_start_h3 = df['start_h3'].unique()
   unique_end_h3 = df['end_h3'].unique()
   
   print(f"📊 Mappatura {len(unique_start_h3)} esagoni origine...")
   for original_h3 in unique_start_h3:
       generalized_h3 = find_generalized_hexagon(original_h3, generalized_start_h3)
       if generalized_h3:
           start_original_to_generalized[original_h3] = generalized_h3
   
   print(f"📊 Mappatura {len(unique_end_h3)} esagoni destinazione...")
   for original_h3 in unique_end_h3:
       generalized_h3 = find_generalized_hexagon(original_h3, generalized_end_h3)
       if generalized_h3:
           end_original_to_generalized[original_h3] = generalized_h3
   
   # 3. Calcola distanze per i punti di partenza
   start_distances = []
   start_coords = []
   
   for idx, row in df.iterrows():
       original_h3 = row['start_h3']
       original_coords = (row['start_lat'], row['start_lon'])
       
       if original_h3 in start_original_to_generalized:
           generalized_h3 = start_original_to_generalized[original_h3]
           generalized_coords = h3.cell_to_latlng(generalized_h3)
           
           distance = geodesic(original_coords, generalized_coords).meters
           
           start_distances.append(distance)
           start_coords.append({
               'original_h3': original_h3,
               'generalized_h3': generalized_h3,
               'original_coords': original_coords,
               'generalized_coords': generalized_coords,
               'distance': distance
           })
   
   # 4. Calcola distanze per i punti di destinazione
   end_distances = []
   end_coords = []
   
   for idx, row in df.iterrows():
       original_h3 = row['end_h3']
       original_coords = (row['end_lat'], row['end_lon'])
       
       if original_h3 in end_original_to_generalized:
           generalized_h3 = end_original_to_generalized[original_h3]
           generalized_coords = h3.cell_to_latlng(generalized_h3)
           
           distance = geodesic(original_coords, generalized_coords).meters
               
           end_distances.append(distance)
           end_coords.append({
               'original_h3': original_h3,
               'generalized_h3': generalized_h3,
               'original_coords': original_coords,
               'generalized_coords': generalized_coords,
               'distance': distance
           })
   
   # 5. Calcola statistiche
   results = {
       'start_distances': {
           'mean': np.mean(start_distances) if start_distances else 0,
           'median': np.median(start_distances) if start_distances else 0,
           'std': np.std(start_distances) if start_distances else 0,
           'min': np.min(start_distances) if start_distances else 0,
           'max': np.max(start_distances) if start_distances else 0,
           'count': len(start_distances)
       },
       'end_distances': {
           'mean': np.mean(end_distances) if end_distances else 0,
           'median': np.median(end_distances) if end_distances else 0,
           'std': np.std(end_distances) if end_distances else 0,
           'min': np.min(end_distances) if end_distances else 0,
           'max': np.max(end_distances) if end_distances else 0,
           'count': len(end_distances)
       },
       'overall': {
           'mean': np.mean(start_distances + end_distances) if (start_distances or end_distances) else 0,
           'median': np.median(start_distances + end_distances) if (start_distances or end_distances) else 0,
           'std': np.std(start_distances + end_distances) if (start_distances or end_distances) else 0,
           'total_points': len(start_distances) + len(end_distances)
       },
       'mappings': {
           'start_original_to_generalized': start_original_to_generalized,
           'end_original_to_generalized': end_original_to_generalized
       },
       'detailed_coords': {
           'start': start_coords,
           'end': end_coords
       }
   }
   
   # 6. Stampa risultati
   print("\n" + "="*60)
   print("📏 METRICHE DI DISTANZA POST-GENERALIZZAZIONE")
   print("="*60)
   
   print(f"\n🎯 PUNTI DI PARTENZA:")
   print(f"   • Distanza media: {results['start_distances']['mean']:.2f} metri")
   print(f"   • Distanza mediana: {results['start_distances']['median']:.2f} metri")
   print(f"   • Deviazione standard: {results['start_distances']['std']:.2f} metri")
   print(f"   • Min-Max: {results['start_distances']['min']:.2f} - {results['start_distances']['max']:.2f} metri")
   print(f"   • Punti analizzati: {results['start_distances']['count']:,}")
   
   print(f"\n🏁 PUNTI DI DESTINAZIONE:")
   print(f"   • Distanza media: {results['end_distances']['mean']:.2f} metri")
   print(f"   • Distanza mediana: {results['end_distances']['median']:.2f} metri")
   print(f"   • Deviazione standard: {results['end_distances']['std']:.2f} metri")
   print(f"   • Min-Max: {results['end_distances']['min']:.2f} - {results['end_distances']['max']:.2f} metri")
   print(f"   • Punti analizzati: {results['end_distances']['count']:,}")
   
   print(f"\n🌍 COMPLESSIVO:")
   print(f"   • Distanza media totale: {results['overall']['mean']:.2f} metri")
   print(f"   • Distanza mediana totale: {results['overall']['median']:.2f} metri")
   print(f"   • Deviazione standard totale: {results['overall']['std']:.2f} metri")
   print(f"   • Punti totali: {results['overall']['total_points']:,}")
   
   return results

def find_generalized_hexagon(original_h3: str, generalized_hexagons: set) -> str:
   """
   Trova l'esagono generalizzato corrispondente a un esagono originale
   """
   # Se l'esagono è già nella lista degli esagoni generalizzati
   if original_h3 in generalized_hexagons:
       return original_h3
   
   # Altrimenti cerca tra tutti gli esagoni generalizzati se l'originale è loro discendente
   for generalized_h3 in generalized_hexagons:
       if is_descendant_of(original_h3, generalized_h3):
           return generalized_h3
   
   return None

def is_descendant_of(child_h3: str, parent_h3: str) -> bool:
   """
   Controlla se child_h3 è discendente di parent_h3
   """
   child_res = h3.get_resolution(child_h3)
   parent_res = h3.get_resolution(parent_h3)
   
   if parent_res >= child_res:
       return False
   
   current = child_h3
   while h3.get_resolution(current) > parent_res:
       current = h3.cell_to_parent(current, h3.get_resolution(current) - 1)
   
   return current == parent_h3

def analyze_generalization_impact(results: Dict) -> None:
   """
   Analizza l'impatto della generalizzazione sulle distanze
   """
   print("\n" + "="*60)
   print("📊 ANALISI IMPATTO GENERALIZZAZIONE")
   print("="*60)
   
   # Calcola percentili
   all_distances = []
   for coord in results['detailed_coords']['start'] + results['detailed_coords']['end']:
       all_distances.append(coord['distance'])
   
   if all_distances:
       percentiles = [25, 50, 75, 90, 95, 99]
       print("\n📏 Distribuzione distanze:")
       for p in percentiles:
           value = np.percentile(all_distances, p)
           print(f"   • {p}° percentile: {value:.2f} metri")
   
   # Analizza per risoluzione
   resolution_analysis = {}
   for coord in results['detailed_coords']['start'] + results['detailed_coords']['end']:
       original_res = h3.get_resolution(coord['original_h3'])
       generalized_res = h3.get_resolution(coord['generalized_h3'])
       
       key = f"{original_res}→{generalized_res}"
       if key not in resolution_analysis:
           resolution_analysis[key] = []
       resolution_analysis[key].append(coord['distance'])
   
   print("\n🔍 Analisi per risoluzione:")
   for resolution_change, distances in resolution_analysis.items():
       mean_dist = np.mean(distances)
       count = len(distances)
       print(f"   • {resolution_change}: {mean_dist:.2f}m (n={count})")

if mode == "SEX":
    print("\n--- METRICHE DISTANZA SEX ---")
    
    print("\n🎯 Uomini:")
    distance_results_man = calculate_generalization_distance_metric(
        df=filtered_df_man, 
        od_matrix_generalized=od_matrix_agg_man
    )
    analyze_generalization_impact(distance_results_man)
    
    print("\n🎯 Donne:")
    distance_results_woman = calculate_generalization_distance_metric(
        df=filtered_df_woman, 
        od_matrix_generalized=od_matrix_agg_woman
    )
    analyze_generalization_impact(distance_results_woman)

elif mode == "AGE":
    print("\n--- METRICHE DISTANZA AGE ---")
    age_labels = ["10_19", "20_29", "30_39", "40_49", "50_59", "60_69", "over70"]
    for label in age_labels:
        print(f"\n🎯 Fascia {label}:")
        distance_results = calculate_generalization_distance_metric(
            df=globals()[f"filtered_df_{label}"], 
            od_matrix_generalized=od_matrix_agg_age_clean[label]  # <- usa il dizionario
        )
        analyze_generalization_impact(distance_results)

elif mode == "PRO_CAT":
    print("\n--- METRICHE DISTANZA PRO_CAT ---")
    for i in range(1, 9):
        key = f"ProCat-{i}"
        print(f"\n🎯 Categoria {key}:")
        distance_results = calculate_generalization_distance_metric(
            df=globals()[f"filtered_df_procat_{i}"], 
            od_matrix_generalized=od_matrix_agg_procat_clean[key]  # <- usa il dizionario
        )
        analyze_generalization_impact(distance_results)

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")


--- METRICHE DISTANZA AGE ---

🎯 Fascia 10_19:
🔍 Calcolo metrica di distanza post-generalizzazione...
📊 Mappatura 594 esagoni origine...
📊 Mappatura 582 esagoni destinazione...

📏 METRICHE DI DISTANZA POST-GENERALIZZAZIONE

🎯 PUNTI DI PARTENZA:
   • Distanza media: 13400.30 metri
   • Distanza mediana: 13262.52 metri
   • Deviazione standard: 2372.98 metri
   • Min-Max: 7730.88 - 21838.68 metri
   • Punti analizzati: 1,837

🏁 PUNTI DI DESTINAZIONE:
   • Distanza media: 13369.23 metri
   • Distanza mediana: 13339.65 metri
   • Deviazione standard: 2288.91 metri
   • Min-Max: 7628.38 - 22316.14 metri
   • Punti analizzati: 1,837

🌍 COMPLESSIVO:
   • Distanza media totale: 13384.77 metri
   • Distanza mediana totale: 13273.94 metri
   • Deviazione standard totale: 2331.37 metri
   • Punti totali: 3,674

📊 ANALISI IMPATTO GENERALIZZAZIONE

📏 Distribuzione distanze:
   • 25° percentile: 11954.49 metri
   • 50° percentile: 13273.94 metri
   • 75° percentile: 14523.77 metri
   • 90° percenti

In [45]:
### Mean Generalisation Error : per ogni flusso anonimizzato, conta quanti esagoni originali sono inclusi nell'area generalizzata (sia per origine che destinazione)
# 
# PAPER:
# Quando le origini e le destinazioni sono aggregate più o meno allo stesso livello (come di solito accade),
# il valore medio 𝐺 rappresenta circa il doppio del numero di celle (esagoni) coinvolte 
# nell'origine o nella destinazione per ogni flusso generalizzato.
# Un valore di 𝐺 = 2 significa quindi che non è stata effettuata alcuna generalizzazione.

class GeneralizationMetric:
    """
    Ḡ = (1/V+) × Σ(|o| + |d|) × v_{o→d}
    """
    def __init__(self, k_threshold: int = 10):
        self.k_threshold = k_threshold

    def calculate_generalization_error(self, od_matrix_generalized: pd.DataFrame, od_matrix: pd.DataFrame) -> float:
        # Costruisci dizionari: generalizzato -> numero di celle originali
        origin_counts = self._build_hexagon_counts(
            od_matrix_generalized, od_matrix, column_gen="start_h3", column_orig="start_h3"
        )
        destination_counts = self._build_hexagon_counts(
            od_matrix_generalized, od_matrix, column_gen="end_h3", column_orig="end_h3"
        )

        total_volume_anonymous = 0
        weighted_count_sum = 0

        for _, row in od_matrix_generalized.iterrows():
            flow_value = row["count"]
            if flow_value >= self.k_threshold:
                origin_h3 = row["start_h3"]
                dest_h3   = row["end_h3"]

                origin_count = origin_counts.get(origin_h3, 1)
                dest_count   = destination_counts.get(dest_h3, 1)

                total_volume_anonymous += flow_value
                weighted_count_sum += (origin_count + dest_count) * flow_value

        return weighted_count_sum / total_volume_anonymous if total_volume_anonymous > 0 else 0.0

    def _build_hexagon_counts(
        self, od_matrix_generalized: pd.DataFrame, od_matrix: pd.DataFrame, 
        column_gen: str, column_orig: str
    ) -> dict:
        """
        Conta quanti esagoni originali appartengono a ciascun esagono generalizzato
        """
        generalized_hexagons = od_matrix_generalized[column_gen].unique()
        original_hexagons = od_matrix[column_orig].unique()

        counts = {}
        for gen_hex in generalized_hexagons:
            target_res = h3.get_resolution(gen_hex)

            # Trova tutti i parent degli originali alla risoluzione target
            parent_series = [h3.cell_to_parent(h, target_res) for h in original_hexagons]

            # Conta quante volte compare il parent == gen_hex
            count = sum(1 for p in parent_series if p == gen_hex)
            counts[gen_hex] = max(count, 1)  # fallback a 1

        return counts
    
metric = GeneralizationMetric(k_threshold=10)

print("\n" + "="*80)
print(f"📊 RISULTATI MEAN GENERALISATION ERROR (Ḡ) | mode = {mode}")
print("="*80)

if mode == "SEX":
    print("\n--- GENERALIZATION ERROR SEX ---")
    error_man = metric.calculate_generalization_error(od_matrix_agg_man, od_matrix_man)
    error_woman = metric.calculate_generalization_error(od_matrix_agg_woman, od_matrix_woman)

    print(f"👨 Uomini   → Ḡ = {error_man:.3f}")
    print(f"👩 Donne    → Ḡ = {error_woman:.3f}")

elif mode == "AGE":
    print("\n--- GENERALIZATION ERROR AGE ---")
    age_labels = ["10_19", "20_29", "30_39", "40_49", "50_59", "60_69", "over70"]
    for label in age_labels:
        print(f"\n🎯 Fascia {label}:")
        error = metric.calculate_generalization_error(
            od_matrix_agg_age_clean[label],  # OD generalizzata pulita
            globals()[f"od_matrix_{label}"]  # OD originale
        )
        print(f"   Ḡ = {error:.3f}")

elif mode == "PRO_CAT":
    print("\n--- GENERALIZATION ERROR PRO_CAT ---")
    for i in range(1, 9):
        key = f"ProCat-{i}"
        print(f"\n🎯 Categoria {key}:")
        error = metric.calculate_generalization_error(
            od_matrix_agg_procat_clean[key],  # OD generalizzata pulita
            globals()[f"od_matrix_procat_{i}"]  # OD originale
        )
        print(f"   Ḡ = {error:.3f}")

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")


📊 RISULTATI MEAN GENERALISATION ERROR (Ḡ) | mode = AGE

--- GENERALIZATION ERROR AGE ---

🎯 Fascia 10_19:
   Ḡ = 1176.000

🎯 Fascia 20_29:
   Ḡ = 3703.983

🎯 Fascia 30_39:
   Ḡ = 3400.213

🎯 Fascia 40_49:
   Ḡ = 3427.540

🎯 Fascia 50_59:
   Ḡ = 2823.588

🎯 Fascia 60_69:
   Ḡ = 2077.156

🎯 Fascia over70:
   Ḡ = 1467.000


In [46]:
def fast_reconstruction_loss(original_od_df: pd.DataFrame,
                                       od_matrix_generalized: pd.DataFrame) -> float:
    """
    Calcola la reconstruction loss includendo anche le celle con 0 viaggi.
    Versione ottimizzata, evita itertools.product su tutte le foglie.
    """
    # Dizionario dei flussi originali
    original_flows = {(row['start_h3'], row['end_h3']): row['count']
                      for _, row in original_od_df.iterrows()}

    total_volume = sum(original_flows.values())
    if total_volume == 0:
        return 0.0

    # Dizionario dei flussi generalizzati
    generalized_flows = {(row['start_h3'], row['end_h3']): row['count']
                         for _, row in od_matrix_generalized.iterrows()}

    gen_start_hexes = od_matrix_generalized['start_h3'].unique()
    gen_end_hexes   = od_matrix_generalized['end_h3'].unique()

    # Cache: gen_hex → leaves
    leaf_cache = {}

    def get_leaves(gen_hex, target_res):
        key = (gen_hex, target_res)
        if key in leaf_cache:
            return leaf_cache[key]
        res = h3.get_resolution(gen_hex)
        leaves = {gen_hex} if res == target_res else set(h3.cell_to_children(gen_hex, target_res))
        leaf_cache[key] = leaves
        return leaves

    # Risoluzione target
    target_res_start = h3.get_resolution(original_od_df['start_h3'].iloc[0])
    target_res_end   = h3.get_resolution(original_od_df['end_h3'].iloc[0])

    # Precompute mappe: leaf → parent generalized
    start_leaf_to_parent = {}
    for gen in gen_start_hexes:
        for leaf in get_leaves(gen, target_res_start):
            start_leaf_to_parent[leaf] = gen

    end_leaf_to_parent = {}
    for gen in gen_end_hexes:
        for leaf in get_leaves(gen, target_res_end):
            end_leaf_to_parent[leaf] = gen

    total_abs_error = 0.0

    # Itera solo sulle coppie presenti nell'originale
    for (s, d), true_count in original_flows.items():
        gen_s = start_leaf_to_parent.get(s)
        gen_d = end_leaf_to_parent.get(d)

        if gen_s is None or gen_d is None:
            reconstructed_count = 0.0
        else:
            gen_count = generalized_flows.get((gen_s, gen_d), 0.0)
            start_leaves = get_leaves(gen_s, target_res_start)
            end_leaves   = get_leaves(gen_d, target_res_end)
            reconstructed_count = gen_count / (len(start_leaves) * len(end_leaves))

        total_abs_error += abs(reconstructed_count - true_count)

    # Aggiungi errore per le coppie con count=0 nei generalized flows
    for (gen_s, gen_d), gen_count in generalized_flows.items():
        start_leaves = get_leaves(gen_s, target_res_start)
        end_leaves   = get_leaves(gen_d, target_res_end)
        count_per_leaf = gen_count / (len(start_leaves) * len(end_leaves))

        # Sottrai le coppie già contate
        for s in start_leaves:
            for d in end_leaves:
                if (s, d) not in original_flows:
                    total_abs_error += abs(count_per_leaf - 0.0)

    return total_abs_error / total_volume


def _find_generalized_parent(original_h3: str, generalized_hexagons: list) -> str:
    """
    Trova l'esagono generalizzato che contiene l'esagono originale.
    """
    original_res = h3.get_resolution(original_h3)
    
    for gen_hex in generalized_hexagons:
        gen_res = h3.get_resolution(gen_hex)
        if gen_res <= original_res:
            parent = h3.cell_to_parent(original_h3, gen_res)
            if parent == gen_hex:
                return gen_hex
    return None

if mode == "SEX":
    print("\n--- RECONSTRUCTION LOSS SEX ---")
    loss_man = fast_reconstruction_loss(
        original_od_df=od_matrix_man,
        od_matrix_generalized=od_matrix_agg_man
    )
    print(f"👨 Uomini   → Reconstruction Loss: {loss_man:.6f}")

    loss_woman = fast_reconstruction_loss(
        original_od_df=od_matrix_woman,
        od_matrix_generalized=od_matrix_agg_woman
    )
    print(f"👩 Donne    → Reconstruction Loss: {loss_woman:.6f}")

elif mode == "AGE":
    print("\n--- RECONSTRUCTION LOSS AGE ---")
    age_labels = ["10_19", "20_29", "30_39", "40_49", "50_59", "60_69", "over70"]
    for label in age_labels:
        print(f"\n🎯 Fascia {label}:")
        loss = fast_reconstruction_loss(
            original_od_df=globals()[f"od_matrix_{label}"],
            od_matrix_generalized=od_matrix_agg_age_clean[label]
        )
        print(f"   Reconstruction Loss: {loss:.6f}")

elif mode == "PRO_CAT":
    print("\n--- RECONSTRUCTION LOSS PRO_CAT ---")
    for i in range(1, 9):
        key = f"ProCat-{i}"
        print(f"\n🎯 Categoria {key}:")
        loss = fast_reconstruction_loss(
            original_od_df=globals()[f"od_matrix_procat_{i}"],
            od_matrix_generalized=od_matrix_agg_procat_clean[key]
        )
        print(f"   Reconstruction Loss: {loss:.6f}")

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")



--- RECONSTRUCTION LOSS AGE ---

🎯 Fascia 10_19:
   Reconstruction Loss: 2.000001

🎯 Fascia 20_29:
   Reconstruction Loss: 1.999990

🎯 Fascia 30_39:
   Reconstruction Loss: 1.999991

🎯 Fascia 40_49:
   Reconstruction Loss: 1.890692

🎯 Fascia 50_59:
   Reconstruction Loss: 1.999993

🎯 Fascia 60_69:
   Reconstruction Loss: 1.581458

🎯 Fascia over70:
   Reconstruction Loss: 1.999999


### Metriche con weights

In [47]:
import numpy as np
import pandas as pd

def compute_discernability_and_cavg(df: pd.DataFrame, k: int, suppressed_count: int = 0) -> dict:
    """
    Calcola C_DM e C_AVG per un dataset OD generalizzato.
    
    Args:
        df: DataFrame con colonne ['start_h3', 'end_h3', 'count']
        k: soglia k-anonimity
        suppressed_count: numero di coppie OD soppressi (facoltativo)
    
    Returns:
        dict con C_DM, C_AVG, numero totale record e classi equivalenza
    """
    counts = df['weight'].values
    total_records = counts.sum() + suppressed_count
    total_equiv_classes = len(counts) + suppressed_count
    total_records_avg = counts.sum()
    total_equiv_classes_avg = len(counts)
    
    # C_DM: somma dei quadrati dei count >= k
    k_anonymous_counts = counts[counts >= k]
    c_dm_gen = np.sum(k_anonymous_counts**2)
    
    # Penalità per record soppressi
    suppression_penalty = suppressed_count * counts.sum()  # o totale record, a seconda della definizione
    c_dm = c_dm_gen + suppression_penalty
    
    # C_AVG: (total_records / total_equiv_classes) / k
    c_avg = (total_records_avg / total_equiv_classes_avg) / k if total_equiv_classes_avg > 0 else float('inf')
    
    return {
        'C_DM': c_dm,
        'C_AVG': c_avg,
        'total_records': total_records,
        'total_equivalence_classes': total_equiv_classes,
        'k': k
    }

if mode == "SEX":
    print("\n--- METRICHE DISCERNIBILITÀ SEX ---")
    
    metrics_man = compute_discernability_and_cavg(od_matrix_agg_man, suppressed_count=suppressed_count_man, k=10*media_peso)
    print("Man:")
    print(f"   C_DM: {metrics_man['C_DM']:,} | C_AVG: {metrics_man['C_AVG']:.4f}")
    
    metrics_woman = compute_discernability_and_cavg(od_matrix_agg_woman, suppressed_count=suppressed_count_woman, k=10*media_peso)
    print("Woman:")
    print(f"   C_DM: {metrics_woman['C_DM']:,} | C_AVG: {metrics_woman['C_AVG']:.4f}")

elif mode == "AGE":
    print("\n--- METRICHE DISCERNIBILITÀ AGE ---")
    age_labels = ["10_19", "20_29", "30_39", "40_49", "50_59", "60_69", "over70"]
    for label in age_labels:
        metrics = compute_discernability_and_cavg(od_matrix_agg_age_clean[label], suppressed_count=suppressed_count_age[label], k=10*media_peso)
        print(f"{label}: C_DM: {metrics['C_DM']:,} | C_AVG: {metrics['C_AVG']:.4f}")

elif mode == "PRO_CAT":
    print("\n--- METRICHE DISCERNIBILITÀ PRO_CAT ---")
    for i in range(1, 9):
        key = f"ProCat-{i}"
        metrics = compute_discernability_and_cavg(od_matrix_agg_procat_clean[key], suppressed_count=suppressed_count_procat[key], k=10*media_peso)
        print(f"{key}: C_DM: {metrics['C_DM']:,} | C_AVG: {metrics['C_AVG']:.4f}")

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")


--- METRICHE DISCERNIBILITÀ AGE ---
10_19: C_DM: 20,521,958,598,003.26 | C_AVG: 169.4032
20_29: C_DM: 30,980,128,143,361.996 | C_AVG: 85.6016
30_39: C_DM: 50,554,864,894,030.375 | C_AVG: 110.2616
40_49: C_DM: 54,215,712,350,171.27 | C_AVG: 65.7745
50_59: C_DM: 40,688,472,212,289.04 | C_AVG: 95.8572
60_69: C_DM: 11,087,064,632,095.658 | C_AVG: 19.0137
over70: C_DM: 11,265,210,245,315.908 | C_AVG: 125.5110


In [48]:
### Mean Generalisation Error : per ogni flusso anonimizzato, conta quanti esagoni originali sono inclusi nell'area generalizzata (sia per origine che destinazione)
# 
# PAPER:
# Quando le origini e le destinazioni sono aggregate più o meno allo stesso livello (come di solito accade),
# il valore medio 𝐺 rappresenta circa il doppio del numero di celle (esagoni) coinvolte 
# nell'origine o nella destinazione per ogni flusso generalizzato.
# Un valore di 𝐺 = 2 significa quindi che non è stata effettuata alcuna generalizzazione.

class GeneralizationMetric:
    """
    Ḡ = (1/V+) × Σ(|o| + |d|) × v_{o→d}
    """
    def __init__(self, k_threshold: int = 10):
        self.k_threshold = k_threshold

    def calculate_generalization_error(self, od_matrix_generalized: pd.DataFrame, od_matrix: pd.DataFrame) -> float:
        # Costruisci dizionari: generalizzato -> numero di celle originali
        origin_counts = self._build_hexagon_counts(
            od_matrix_generalized, od_matrix, column_gen="start_h3", column_orig="start_h3"
        )
        destination_counts = self._build_hexagon_counts(
            od_matrix_generalized, od_matrix, column_gen="end_h3", column_orig="end_h3"
        )

        total_volume_anonymous = 0
        weighted_count_sum = 0

        for _, row in od_matrix_generalized.iterrows():
            flow_value = row["weight"]
            if flow_value >= self.k_threshold:
                origin_h3 = row["start_h3"]
                dest_h3   = row["end_h3"]

                origin_count = origin_counts.get(origin_h3, 1)
                dest_count   = destination_counts.get(dest_h3, 1)

                total_volume_anonymous += flow_value
                weighted_count_sum += (origin_count + dest_count) * flow_value

        return weighted_count_sum / total_volume_anonymous if total_volume_anonymous > 0 else 0.0

    def _build_hexagon_counts(
        self, od_matrix_generalized: pd.DataFrame, od_matrix: pd.DataFrame, 
        column_gen: str, column_orig: str
    ) -> dict:
        """
        Conta quanti esagoni originali appartengono a ciascun esagono generalizzato
        """
        generalized_hexagons = od_matrix_generalized[column_gen].unique()
        original_hexagons = od_matrix[column_orig].unique()

        counts = {}
        for gen_hex in generalized_hexagons:
            target_res = h3.get_resolution(gen_hex)

            # Trova tutti i parent degli originali alla risoluzione target
            parent_series = [h3.cell_to_parent(h, target_res) for h in original_hexagons]

            # Conta quante volte compare il parent == gen_hex
            count = sum(1 for p in parent_series if p == gen_hex)
            counts[gen_hex] = max(count, 1)  # fallback a 1

        return counts
    
metric = GeneralizationMetric(k_threshold=10*media_peso)

print("\n" + "="*80)
print(f"📊 RISULTATI MEAN GENERALISATION ERROR (Ḡ) | mode = {mode}")
print("="*80)

if mode == "SEX":
    print("\n--- GENERALIZATION ERROR SEX ---")
    error_man = metric.calculate_generalization_error(od_matrix_agg_man, od_matrix_man)
    error_woman = metric.calculate_generalization_error(od_matrix_agg_woman, od_matrix_woman)

    print(f"👨 Uomini   → Ḡ = {error_man:.3f}")
    print(f"👩 Donne    → Ḡ = {error_woman:.3f}")

elif mode == "AGE":
    print("\n--- GENERALIZATION ERROR AGE ---")
    age_labels = ["10_19", "20_29", "30_39", "40_49", "50_59", "60_69", "over70"]
    for label in age_labels:
        print(f"\n🎯 Fascia {label}:")
        error = metric.calculate_generalization_error(
            od_matrix_agg_age_clean[label],  # OD generalizzata pulita
            globals()[f"od_matrix_{label}"]  # OD originale
        )
        print(f"   Ḡ = {error:.3f}")

elif mode == "PRO_CAT":
    print("\n--- GENERALIZATION ERROR PRO_CAT ---")
    for i in range(1, 9):
        key = f"ProCat-{i}"
        print(f"\n🎯 Categoria {key}:")
        error = metric.calculate_generalization_error(
            od_matrix_agg_procat_clean[key],  # OD generalizzata pulita
            globals()[f"od_matrix_procat_{i}"]  # OD originale
        )
        print(f"   Ḡ = {error:.3f}")

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")


📊 RISULTATI MEAN GENERALISATION ERROR (Ḡ) | mode = AGE

--- GENERALIZATION ERROR AGE ---

🎯 Fascia 10_19:
   Ḡ = 1176.000

🎯 Fascia 20_29:
   Ḡ = 3704.090

🎯 Fascia 30_39:
   Ḡ = 3385.131

🎯 Fascia 40_49:
   Ḡ = 3451.347

🎯 Fascia 50_59:
   Ḡ = 2829.993

🎯 Fascia 60_69:
   Ḡ = 2085.991

🎯 Fascia over70:
   Ḡ = 1467.000


In [49]:
def fast_reconstruction_loss(original_od_df: pd.DataFrame,
                                       od_matrix_generalized: pd.DataFrame) -> float:
    """
    Calcola la reconstruction loss includendo anche le celle con 0 viaggi.
    Versione ottimizzata, evita itertools.product su tutte le foglie.
    """
    # Dizionario dei flussi originali
    original_flows = {(row['start_h3'], row['end_h3']): row['total_weight']
                      for _, row in original_od_df.iterrows()}

    total_volume = sum(original_flows.values())
    if total_volume == 0:
        return 0.0

    # Dizionario dei flussi generalizzati
    generalized_flows = {(row['start_h3'], row['end_h3']): row['weight']
                         for _, row in od_matrix_generalized.iterrows()}

    gen_start_hexes = od_matrix_generalized['start_h3'].unique()
    gen_end_hexes   = od_matrix_generalized['end_h3'].unique()

    # Cache: gen_hex → leaves
    leaf_cache = {}

    def get_leaves(gen_hex, target_res):
        key = (gen_hex, target_res)
        if key in leaf_cache:
            return leaf_cache[key]
        res = h3.get_resolution(gen_hex)
        leaves = {gen_hex} if res == target_res else set(h3.cell_to_children(gen_hex, target_res))
        leaf_cache[key] = leaves
        return leaves

    # Risoluzione target
    target_res_start = h3.get_resolution(original_od_df['start_h3'].iloc[0])
    target_res_end   = h3.get_resolution(original_od_df['end_h3'].iloc[0])

    # Precompute mappe: leaf → parent generalized
    start_leaf_to_parent = {}
    for gen in gen_start_hexes:
        for leaf in get_leaves(gen, target_res_start):
            start_leaf_to_parent[leaf] = gen

    end_leaf_to_parent = {}
    for gen in gen_end_hexes:
        for leaf in get_leaves(gen, target_res_end):
            end_leaf_to_parent[leaf] = gen

    total_abs_error = 0.0

    # Itera solo sulle coppie presenti nell'originale
    for (s, d), true_count in original_flows.items():
        gen_s = start_leaf_to_parent.get(s)
        gen_d = end_leaf_to_parent.get(d)

        if gen_s is None or gen_d is None:
            reconstructed_count = 0.0
        else:
            gen_count = generalized_flows.get((gen_s, gen_d), 0.0)
            start_leaves = get_leaves(gen_s, target_res_start)
            end_leaves   = get_leaves(gen_d, target_res_end)
            reconstructed_count = gen_count / (len(start_leaves) * len(end_leaves))

        total_abs_error += abs(reconstructed_count - true_count)

    # Aggiungi errore per le coppie con count=0 nei generalized flows
    for (gen_s, gen_d), gen_count in generalized_flows.items():
        start_leaves = get_leaves(gen_s, target_res_start)
        end_leaves   = get_leaves(gen_d, target_res_end)
        count_per_leaf = gen_count / (len(start_leaves) * len(end_leaves))

        # Sottrai le coppie già contate
        for s in start_leaves:
            for d in end_leaves:
                if (s, d) not in original_flows:
                    total_abs_error += abs(count_per_leaf - 0.0)

    return total_abs_error / total_volume


def _find_generalized_parent(original_h3: str, generalized_hexagons: list) -> str:
    """
    Trova l'esagono generalizzato che contiene l'esagono originale.
    """
    original_res = h3.get_resolution(original_h3)
    
    for gen_hex in generalized_hexagons:
        gen_res = h3.get_resolution(gen_hex)
        if gen_res <= original_res:
            parent = h3.cell_to_parent(original_h3, gen_res)
            if parent == gen_hex:
                return gen_hex
    return None

if mode == "SEX":
    print("\n--- RECONSTRUCTION LOSS SEX ---")
    loss_man = fast_reconstruction_loss(
        original_od_df=od_matrix_man,
        od_matrix_generalized=od_matrix_agg_man
    )
    print(f"👨 Uomini   → Reconstruction Loss: {loss_man:.6f}")

    loss_woman = fast_reconstruction_loss(
        original_od_df=od_matrix_woman,
        od_matrix_generalized=od_matrix_agg_woman
    )
    print(f"👩 Donne    → Reconstruction Loss: {loss_woman:.6f}")

elif mode == "AGE":
    print("\n--- RECONSTRUCTION LOSS AGE ---")
    age_labels = ["10_19", "20_29", "30_39", "40_49", "50_59", "60_69", "over70"]
    for label in age_labels:
        print(f"\n🎯 Fascia {label}:")
        loss = fast_reconstruction_loss(
            original_od_df=globals()[f"od_matrix_{label}"],
            od_matrix_generalized=od_matrix_agg_age_clean[label]
        )
        print(f"   Reconstruction Loss: {loss:.6f}")

elif mode == "PRO_CAT":
    print("\n--- RECONSTRUCTION LOSS PRO_CAT ---")
    for i in range(1, 9):
        key = f"ProCat-{i}"
        print(f"\n🎯 Categoria {key}:")
        loss = fast_reconstruction_loss(
            original_od_df=globals()[f"od_matrix_procat_{i}"],
            od_matrix_generalized=od_matrix_agg_procat_clean[key]
        )
        print(f"   Reconstruction Loss: {loss:.6f}")

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")



--- RECONSTRUCTION LOSS AGE ---

🎯 Fascia 10_19:
   Reconstruction Loss: 2.000000

🎯 Fascia 20_29:
   Reconstruction Loss: 1.999990

🎯 Fascia 30_39:
   Reconstruction Loss: 1.999992

🎯 Fascia 40_49:
   Reconstruction Loss: 1.884190

🎯 Fascia 50_59:
   Reconstruction Loss: 1.999993

🎯 Fascia 60_69:
   Reconstruction Loss: 1.568172

🎯 Fascia over70:
   Reconstruction Loss: 1.999999
